# Estructura de la materia 3
## Trabajo final: DFT de Helio en GS
### PARTE C: Inclusión del potencial de correlación
Mendez, Alejandra

In [83]:
%matplotlib inline

In [84]:
from numpy import sqrt, exp, linspace, zeros, identity, array, diag, c_, pi, log
from math import factorial
from numpy.linalg import eigh
from scipy.integrate import quad
from scipy.special import hyp1f1
from matplotlib.pyplot import plot, axis, title, xlabel, ylabel, show,\
                              legend, subplot

In [85]:
# Normalización de las funciones 
def Normalizate(U,x):
    h = x[1]-x[0] # assume uniformly spaced points
    n = len(x)
    for j in range(0,n-1):
        suma = 0.0
        for i in range(0,n-1):
             suma = suma + U[i,j]**2
        #suma = suma + U[0,j]/2.0
        suma = suma*h 
        rnorm = 1/sqrt(suma)
#       Normalization
        rsign = 1
        if U[1,j] < 0:
            rsign = -1
        rnorm = rnorm * rsign
        for i in range(0,n):
            U[i,j] = U[i,j]*rnorm
    return  U

In [86]:
def Laplacian(x):
    h = x[1]-x[0] # assume uniformly spaced points
    n = len(x)
    M = -2*identity(n,'d')
    for i in range(1,n):
        M[i,i-1] = M[i-1,i] = 1
    return M/h**2

In [4]:
# Defino las dimensiones de los arrays a utilizar
nsize = 2000
rmax = 10.0
h = rmax/nsize
rmin = h

In [5]:
print(h)

0.005


In [6]:
# Defino las matrices y vectores necesarios
r = linspace(rmin,rmax,nsize)
T = array([nsize,nsize])
Vs = array([nsize,nsize])
U = zeros([nsize,nsize])
H = array([nsize,nsize])
E = array([nsize])

In [7]:
den = zeros(nsize)
Vh = zeros(nsize)
Vx = zeros(nsize)
Vc = zeros(nsize)

In [8]:
# Defino el sistema a resolver: Helio en el estado fundamental
Z = 2
l = 0

In [9]:
# Defino la densidad total
def densidad():
    noc = 2.0      # nro de ocupacion = 1 
    ang = 1.0/(4.0*pi)
    for i in range(nsize):
        den[i] = noc*(U[i,0]/r[i])**2*ang
    return den

In [10]:
# Defino el potencial de Hartree
# Uso el índice j (nro de iteracion) para no incluir el potencial Vh en la primera iteración
def VHartree(j):
    Upp = zeros(nsize)
    Up = zeros(nsize)
    Zh = zeros(nsize)
    if (j>0):
        # 1ra condicion de borde
        Up[0] = 0.0
        Zh[0] = 0.0
        Zh[1] = h
        for i in range(nsize):
            Upp[i] = -4.0*pi*den[i]*r[i]
        for i in range(nsize-1):
            Up[i+1] = Up[i] + 0.5*(Upp[i] + Upp[i+1])*h 
        # 2da condicion de borde
        alfa = -Up[nsize-1]
        for i in range(nsize-1):
            Zh[i+1] = Zh[i] + Up[i]*h + 0.5*Upp[i]*h**2 
        for i in range(nsize):
            Zh[i] = Zh[i] + alfa*r[i]
        for i in range(nsize):
            Vh[i] = Zh[i]/r[i]
    return Vh

In [11]:
# Defino el potencial de Exchange: Local Density Approximation (Slater)
# Nuevamente uso j para no incluir el potencial en la primera iteración
def Vexchange(j):
    if (j>0):
        Ax = -(3./pi)**(1./3.)
        for i in range(nsize):
            Vx[i] = Ax*(den[i])**(1./3.)
    return Vx

La ecuación de Kohn-Sham está dada por 
\begin{equation}
  \left[-\frac{1}{2}\nabla^2 + V_{\mathrm{s}}\left(n|\mathbf{r}\right)\right] \phi_i = \epsilon_i \phi_i
\end{equation}

donde

\begin{equation}
  V_{\mathrm{s}}(n|\mathbf{r}) = V_{\mathrm{ext}}(r) + V_{\mathrm{H}}(n|\mathbf{r}) + V_{\mathrm{x}}(n|\mathbf{r}) + V_{\mathrm{c}}(n|\mathbf{r}) 
\end{equation}

El potencial de Hartree está dado por:

\begin{equation}
   V_{\mathrm{H}}(r) = \int{d\mathbf{r}\,\frac{n(\mathbf{r}')}{\left|\mathbf{r}-\mathbf{r}'\right|}}
\end{equation}

donde $n=\sum_i{n_i}=\sum_i{\left|\phi_i\right|^2}$ es la densidad total.

\begin{equation}
   \quad \Rightarrow \quad 
   \nabla^2 V_{\mathrm{H}}(n|\mathbf{r}) = -4\pi \, n(\mathbf{r})
\end{equation}

Debido a la simetría radial de la densidad,

\begin{equation}
  Z_{\mathrm{H}}(r) = r V_{\mathrm{H}}(r) 
   \quad \Rightarrow \quad 
   \frac{d^2 Z_{\mathrm{H}}(r)}{dr^2} = -4\pi \, r\,n(r)
\end{equation}

Resuelvo usando el algoritmo de Verlet, e imponiendo dos condiciones 
de borde

\begin{equation}
  Z_{\mathrm{H}}(0) = 0
  \quad \mbox{y} \quad  
  Z_{\mathrm{H}}(r_{\mathrm{max}}) = q = 2
\end{equation}

El potencial de exchange está dado por la Local Density Approximation (LDA) formulada por Slater:

\begin{equation}
   V_{\mathrm{x}}(r) = A_{\mathrm{x}}n(r)^{1/3} \quad : \quad A_{\mathrm{x}} = -(3/\pi)^{1/3}
\end{equation}


El potencial de correlación de Perdew-Zunger (parametrización de Ceperley-Alder's Quantum Monte Carlo calculations)

\begin{equation}
\begin{split}
r_s = \left(\frac{3}{4\pi n(r)}\right)^{1/3} &\\
\varepsilon_c(r) = \frac{\gamma}{1+\beta_1\sqrt{r_s}+\beta_2 r_s} &\\
   r_s \geq 1 \quad : \quad V_{\mathrm{c}}(r) &= \varepsilon_c(r)\frac{1 + 7/6 \beta_1\sqrt{r_s} + \beta_2r_s}{1.0 + \beta_1\sqrt{r_s} + \beta_2r_s} \\
   r_s \lt 1 \quad : \quad V_{\mathrm{c}}(r) &=  A\log{r_s} + B - A/3 + \tfrac{2}{3}Cr_s\log{r_s} + (2D-C)r_s/3  \\
\end{split}
\end{equation}

In [12]:
# Defino el potencial de Correlación: 
# Perdew-Zunger parametrization of Ceperley-Alder Approximation (Quantum Monte Carlo) 
# Nuevamente uso j para no incluir el potencial en la primera iteración
def Vcorrelation(j):
    rs = zeros(nsize)
    ec = zeros(nsize)
    gamma = -0.1423
    beta1 = 1.0529
    beta2 = 0.3334
    A = 0.0311
    B = -0.048
    C = 0.0020
    D = -0.0116
    if (j>0):
        for i in range(nsize):
            rs[i] = (3.0/(4.0*pi*den[i]))**(1./3.)
            if (rs[i]>=1.0):
                deno = 1.0 + beta1*sqrt(rs[i]) + beta2*rs[i]
                ec[i] = gamma/deno
                num = 1.0 + 7.0/6.0*beta1*sqrt(rs[i]) + beta2*rs[i]
                Vc[i] = ec[i]*num/deno
            if (rs[i]<1.0):
                Vc[i] = A*log(rs[i]) + B - A/3.0 + (2.0/3.0)*C*rs[i]*log(rs[i]) + (2.0*D-C)*rs[i]/3.0
    return Vc

In [13]:
# Inicializo algunas variables utiles en la iteración
# j : nro de iteraciones
j = 0
Eorb = []
u0 = zeros((nsize,1))

## Empieza loop

In [74]:
# Calculo la densidad, el potencial de Hartree, potencial de Exchange LDA
# y potencial de correlación de Perdew-Zunger
densidad()
VHartree(j)
Vexchange(j)
Vcorrelation(j)

# Construyo el operador T y el operador Vs (potencial efectivo)
T = (-0.5)*Laplacian(r)
Vs = -Z/r + l*(l+1)/(2*r**2) + Vh + Vx + Vc

In [75]:
# Construyo el Hamiltoniano del sistema
H =  T + diag(Vs)

In [76]:
# Calculo autovalores (E) y autovectores (U)
E,U = eigh(H)
j = j + 1

# Normalization
U = Normalizate(U,r)

In [77]:
# Corroboro normalización
suma = 0.0
for i in range(nsize):
    suma = suma + (U[i,0])**2
suma = suma*h
suma

1.0000000000000051

In [78]:
# Adjunto los resultados para ver los resultados de cada iteración
# Eorb : energías
# u0   : funciones radiales reducidas
Eorb.append(E[0])
Eorb

[-1.9999500024997479,
 -0.37792037238996018,
 -0.66361178642871488,
 -0.53006082479023342,
 -0.58463723778853394,
 -0.56066344544776547,
 -0.5708991277223342,
 -0.56647247169253911,
 -0.56837638127262669,
 -0.5675555710941057,
 -0.56790907815853653]

In [79]:
u0 = c_[u0,U[:,0]]
u0

array([[  0.00000000e+00,   2.80021427e-02,   2.10798631e-02, ...,
          2.33171319e-02,   2.33086089e-02,   2.33122809e-02],
       [  0.00000000e+00,   5.54470427e-02,   4.17408700e-02, ...,
          4.61706036e-02,   4.61537285e-02,   4.61609989e-02],
       [  0.00000000e+00,   8.23430168e-02,   6.19899184e-02, ...,
          6.85677038e-02,   6.85426458e-02,   6.85534416e-02],
       ..., 
       [  0.00000000e+00,   6.57646999e-09,   1.08478474e-05, ...,
          2.61819746e-06,   2.63322047e-06,   2.62673867e-06],
       [  0.00000000e+00,   4.38398456e-09,   7.23178440e-06, ...,
          1.74542364e-06,   1.75543880e-06,   1.75111768e-06],
       [  0.00000000e+00,   2.19189365e-09,   3.61585804e-06, ...,
          8.72699419e-07,   8.77706948e-07,   8.75546408e-07]])

## Termina loop

La energía total en este esquema está dada por:

\begin{equation}
  E = \sum_i\epsilon_i - E_{\mathrm{H}} - E_{\mathrm{x}} + E_{\mathrm{c}}
\end{equation}
siendo

\begin{equation}
  E_{\mathrm{H}} = \frac{1}{2} \int{dr \,V_{\mathrm{H}}(r)\,n(r) }\,, \quad 
  E_{\mathrm{x}} = \frac{1}{2} \int{dr \,V_{\mathrm{x}}(r)\,n(r) }  \quad \mbox{y} \quad
  E_{\mathrm{c}} = \int{dr \,V_{\mathrm{c}}(r)\,n(r) } 
\end{equation}

In [81]:
# Calculo la integral del potencial Vh
suma = 0.0
for i in range(nsize):
    suma = suma + Vh[i]*(U[i,0]**2)
Eh = suma*h
print('Eh = ',Eh)
# Calculo la integral del potencial Vx
suma = 0.0
for i in range(nsize):
    suma = suma + Vx[i]*(U[i,0]**2)
Ex = 0.5*suma*h
print('Ex = ',Ex)
# Calculo la integral del potencial Vc
suma = 0.0
for i in range(nsize):
    suma = suma + Vc[i]*(U[i,0]**2)
Ec = suma*h
print('Ec = ',Ec)

Eh =  1.9967230724
Ex =  -0.287382121898
Ec =  -0.0608743171267


### Energia correlacion Expt : -0.042 a.u.

In [82]:
# Calculo la energia total del sistema
for i in range(j):
    if (i==0):
        Etot = 2.0*(Eorb[i])
    else:
        Etot = 2.0*(Eorb[i]) - Eh - Ex + Ec
    print('# de iteracion:',i,'  Etot = ',Etot)

# de iteracion: 0   Etot =  -3.999900005
# de iteracion: 1   Etot =  -2.52605601241
# de iteracion: 2   Etot =  -3.09743884048
# de iteracion: 3   Etot =  -2.83033691721
# de iteracion: 4   Etot =  -2.9394897432
# de iteracion: 5   Etot =  -2.89154215852
# de iteracion: 6   Etot =  -2.91201352307
# de iteracion: 7   Etot =  -2.90316021101
# de iteracion: 8   Etot =  -2.90696803017
# de iteracion: 9   Etot =  -2.90532640981
# de iteracion: 10   Etot =  -2.90603342394


### Energia total : -2.90368 a.u.